In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import copy


In [2]:
data = pd.read_csv("../data/txn_by_dept.csv")
data.head()

POS Txn                       Dept   ID  Sales U
0  16120100160021008773               0261:HOSIERY  250        2
1  16120100160021008773  0634:VITAMINS & HLTH AIDS  102        1
2  16120100160021008773          0879:PET SUPPLIES  158        2
3  16120100160021008773                 0973:CANDY  175        2
4  16120100160021008773               0982:SPIRITS  176        1

In [3]:
depts = set(data['Dept'])
transactions = set(data['POS Txn'])
data["ID"] = data["ID"].astype(str)
ids = set(data["ID"])

In [4]:
print(ids)

{'11', '106', '22', '132', '135', '28', '171', '277', '150', '5', '165', '104', '82', '3', '122', '272', '264', '111', '19', '36', '54', '44', '70', '79', '45', '58', '99', '56', '24', '214', '131', '8', '200', '81', '155', '18', '42', '307', '202', '204', '242', '74', '296', '144', '288', '61', '60', '49', '184', '29', '270', '266', '305', '85', '51', '40', '23', '52', '32', '63', '185', '278', '311', '57', '178', '71', '138', '235', '151', '166', '294', '75', '113', '309', '134', '158', '128', '86', '1', '93', '169', '38', '55', '27', '107', '167', '143', '26', '35', '14', '250', '177', '65', '80', '152', '64', '6', '2', '108', '154', '12', '148', '9', '269', '37', '13', '273', '77', '110', '183', '17', '53', '219', '156', '46', '100', '160', '78', '308', '31', '34', '48', '102', '94', '30', '7', '306', '59', '157', '105', '310', '73', '72', '133', '175', '21', '164', '170', '265', '297', '268', '149', '146', '41', '182', '147', '10', '213', '97', '295', '179', '141', '50', '263', '7

In [5]:
adj_matrix = pd.DataFrame(columns = ids, index = transactions, data = np.zeros((len(transactions), len(ids))))
for row in data.iterrows():
    adj_matrix[row[1][2]].loc[row[1][0]] += 1


# mask = adj_matrix>=1
# adj_matrix_binary = adj_matrix.mask(adj_matrix >= 1, 1)
adj_matrix.head()   

11  106   22  132  135   28  171  277  150    5  ...  \
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005061  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  ...   
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   

                      179  141   50  263   76  109   87  176  292  129  
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005061  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 160 columns]

In [6]:
support = []
relative_support = []
for col in adj_matrix.columns: 
    support.append(adj_matrix[col].sum())
    relative_support.append(adj_matrix[col].sum()/len(adj_matrix))


In [7]:
def get_candidates(k, frequents):
    j = k-1
    candidates = []    
    if k > 1:
#             print('here ', k)
            for f1 in range(len(frequents)):
                for f2 in range(f1+1, len(frequents)):
                    if frequents[f1][0:j]==frequents[f2][0:j]:
#                         print('f1', frequents[f1][0:j+1])
#                         print('f2', frequents[f2][j:])
                        candidates.append(frequents[f1][0:j+1]+frequents[f2][j:])
#             print('candidates:', ca    # just work w    # just work way through by removing one each timeay through by removing one each timendidates)
    else:
        for f1 in range(len(frequents)):
            for f2 in range(f1+1, len(frequents)):
                candidates.append([frequents[f1],frequents[f2]])
    
    return candidates

In [8]:
def frequent_item_sets(adj_matrix, C1_itemset, min_sup):
    support_dict = {}
    binary_matrix = adj_matrix.copy()
    max_itemset = len(C1_itemset)
    candidates = C1_itemset
    
    frequents = []
    supports = []
    for candidate in candidates:
        support = binary_matrix[candidate].sum()
        

        if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

    if len(frequents) == 0:
        return support_dict

    support_dict[1] = [frequents, supports]
    candidates = get_candidates(1, frequents)
                    
    for k in range(2, max_itemset):
        print(k)
        frequents = []
        supports = []
        for candidate in candidates:
            support = binary_matrix.where(binary_matrix[candidate].sum(axis=1) == len(candidate)).sum().max()
#             support = binary_matrix[candidate].sum()
            if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

                
        if len(frequents) == 0:
            print('No Frequents')
            return support_dict
        
        support_dict[k] = [frequents, supports]
#         print(frequents)
        
        
        candidates = get_candidates(k, frequents)
#         print('full candidates ', candidates)
        candidates = prune_candidates(candidates, frequents)
#         print('pruned ', candidates)

    return support_dict

In [9]:
def prune_candidates(candidates, frequent_set):
    pruned_list = []
    
    for c in range(len(candidates)):
        prune_flag = False
        for i in range(len(candidates[c])):
#             try:
            temp = copy.deepcopy(candidates[c])
            temp.pop(i)
            if temp not in frequent_set:
                prune_flag = True
                break
        if not prune_flag:
            pruned_list.append(candidates[c])
#             except:
#                 print('candidate ', candidates[c])
#                 print('temp', temp)
#                 print('pruned_list', pruned_list)
    return pruned_list

In [10]:
def get_antecedents(parent_set, frequency_dict, max_key):
    antecedents = []
    for key in frequency_dict.keys():
        if key < max_key:
            f_set = frequency_dict[key]
            print('f_set', list(f_set[0][1]))
#             print('f_set_can', f_set[0])
#             print('f_set_sup', f_set[1])
            for i in range(len(f_set[0])):
                print(f_set[0][i])
                if len(list(f_set[0][i]))==1:
                    temp = [f_set[0][i]]
                else:
                    temp = f_set[0][i]
#                 print(set(temp))
#                 print(set(parent_set))
                if set(temp).issubset(set(parent_set)):
#                     print(temp,f_set[1][i])
                    antecedents.append([temp,f_set[1][i]])
                
        else:
            break
                                        
                    
    return antecedents
                
    

In [11]:
def get_association_rules(frequency_dict, min_conf):
    confidence_dict = []
    for key in frequency_dict.keys():
        if key > 1:
            for i in range(len(frequency_dict[key][0])):
                z = frequency_dict[key][0][i]
                z_sup = frequency_dict[key][1][i]
                print('parent set: ', z, z_sup)
                antecedents = get_antecedents(z, frequency_dict, key)
#                 print('antecedents: ', antecedents)
                
#                 for antecedent in antecedents:
                while len(antecedents) > 0:
                    antecedent = antecedents.pop()
                    x = set(antecedent[0])
                    x_sup = antecedent[1]
                    print('X', x, x_sup)
                    y = set(z)-x
#                     for compliment in antecedents:
#                         if set(compliment[0]) == y:
#                             y_sup = compliment[1]
#                             print('Y', y, y_sup)
                    confidence = z_sup/x_sup
                    print(x, '->', y, confidence)
                    if confidence >= min_conf:
                        confidence_dict.append([list(x),list(y), confidence])
                    else:
                        antecedents = prune_antecedents(x, antecedents)
#                         print('pruned', antecedents)
                            
    return confidence_dict

In [12]:
def prune_antecedents(x, antecedents):
    pruned_antecedents = []
    for antecedent in antecedents:
        if set(antecedent[0]).issubset(x):
            pass
        else:
            pruned_antecedents.append(antecedent)
            
    return pruned_antecedents

In [13]:
def get_evals(confidences_list, frequency_dict, size_dataset):
    metrics = []
    for c in confidences_list:
        print('\n', c)
        confidence = c[2]
        k = len(c[1])
        frequencies = frequency_dict[k]
#         print('frequencies 0', frequencies[0])
#         print('c1', set(c[1]))
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
#             print('temp', temp)
            if set(c[1])==temp:
                support = frequencies[1][i]
        lift = confidence/(support/size_dataset)
        print('lift', lift)
        
        c.append(lift)
        
        # leverage = rel_sup(XY) - rel(x)*rel(y)
        x = set(c[0])
        y = set(c[1])
        xy = x.union(y)
#         print(x)
#         print(y)
#         print(xy)
        k = len(xy)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if xy==temp:
                support_xy = frequencies[1][i]
        rel_xy = support_xy/size_dataset
        
        x = set(c[0])
        k = len(x)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if x==temp:
                support_x = frequencies[1][i]
        rel_x = support_x/size_dataset
        
        y = set(c[1])
        k = len(y)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if y==temp:
                support_y = frequencies[1][i]
        rel_y = support_y/size_dataset
        
        leverage = rel_xy - rel_x*rel_y
        print('leverage', leverage)
        
        c.append(leverage)
        metrics.append([lift, leverage])
        
    return confidences_list, metrics

In [14]:
test1 = [
[1, 0, 1, 1, 0, 0],
[0, 1, 0, 1, 0, 0],
[1, 1, 1, 0, 1, 0],
[0, 1, 0, 1, 0, 1]#,
# [1, 1, 1, 1, 1, 0]
]

test2 = [
[1, 1, 1, 0, 0],
[1, 1, 1, 1, 1],
[1, 0, 1, 1, 0],
[1, 0, 1, 1, 1],
[1, 1, 1, 1, 0]
]

In [15]:
test_df = pd.DataFrame(data=test2, columns = ['A', 'B', 'C', 'D', 'E'])
test_df.head()

A  B  C  D  E
0  1  1  1  0  0
1  1  1  1  1  1
2  1  0  1  1  0
3  1  0  1  1  1
4  1  1  1  1  0

In [16]:
frequent_test = frequent_item_sets(test_df, test_df.columns, 2)
print('\n')
for key in frequent_test.keys():
    print('Item Set Length: ', key, '\n', frequent_test[key][0], '\n', frequent_test[key][1])

2
3
4


Item Set Length:  1 
 ['A', 'B', 'C', 'D', 'E'] 
 [5, 3, 5, 4, 2]
Item Set Length:  2 
 [['A', 'B'], ['A', 'C'], ['A', 'D'], ['A', 'E'], ['B', 'C'], ['B', 'D'], ['C', 'D'], ['C', 'E'], ['D', 'E']] 
 [3.0, 5, 4.0, 2.0, 3.0, 2.0, 4.0, 2.0, 2.0]
Item Set Length:  3 
 [['A', 'B', 'C'], ['A', 'B', 'D'], ['A', 'C', 'D'], ['A', 'C', 'E'], ['A', 'D', 'E'], ['B', 'C', 'D'], ['C', 'D', 'E']] 
 [3.0, 2.0, 4.0, 2.0, 2.0, 2.0, 2.0]
Item Set Length:  4 
 [['A', 'B', 'C', 'D'], ['A', 'C', 'D', 'E']] 
 [2.0, 2.0]


In [17]:
confidence_test = get_association_rules(frequent_test, 1)

parent set:  ['A', 'B'] 3.0
f_set ['B']
A
B
C
D
E
X {'B'} 3
{'B'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'B'} 0.6
parent set:  ['A', 'C'] 5
f_set ['B']
A
B
C
D
E
X {'C'} 5
{'C'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'C'} 1.0
parent set:  ['A', 'D'] 4.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'D'} 0.8
parent set:  ['A', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'E'} 0.4
parent set:  ['B', 'C'] 3.0
f_set ['B']
A
B
C
D
E
X {'C'} 5
{'C'} -> {'B'} 0.6
X {'B'} 3
{'B'} -> {'C'} 1.0
parent set:  ['B', 'D'] 2.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'B'} 0.5
X {'B'} 3
{'B'} -> {'D'} 0.6666666666666666
parent set:  ['C', 'D'] 4.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'C'} 1.0
X {'C'} 5
{'C'} -> {'D'} 0.8
parent set:  ['C', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'C'} 1.0
X {'C'} 5
{'C'} -> {'E'} 0.4
parent set:  ['D', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'D'} 1.0
X {'D'} 4
{'D'} -> {'E'} 0.5
parent set:  ['

In [18]:
for c in confidence_test:
    print(c)

[['B'], ['A'], 1.0]
[['C'], ['A'], 1.0]
[['A'], ['C'], 1.0]
[['D'], ['A'], 1.0]
[['E'], ['A'], 1.0]
[['B'], ['C'], 1.0]
[['D'], ['C'], 1.0]
[['E'], ['C'], 1.0]
[['E'], ['D'], 1.0]
[['B', 'C'], ['A'], 1.0]
[['B', 'A'], ['C'], 1.0]
[['B'], ['A', 'C'], 1.0]
[['D', 'B'], ['A'], 1.0]
[['D', 'C'], ['A'], 1.0]
[['D', 'A'], ['C'], 1.0]
[['D'], ['A', 'C'], 1.0]
[['C', 'E'], ['A'], 1.0]
[['A', 'E'], ['C'], 1.0]
[['E'], ['A', 'C'], 1.0]
[['D', 'E'], ['A'], 1.0]
[['A', 'E'], ['D'], 1.0]
[['E'], ['D', 'A'], 1.0]
[['D', 'B'], ['C'], 1.0]
[['D', 'E'], ['C'], 1.0]
[['C', 'E'], ['D'], 1.0]
[['E'], ['D', 'C'], 1.0]
[['D', 'B', 'C'], ['A'], 1.0]
[['D', 'B', 'A'], ['C'], 1.0]
[['D', 'B'], ['A', 'C'], 1.0]
[['D', 'C', 'E'], ['A'], 1.0]
[['D', 'A', 'E'], ['C'], 1.0]
[['A', 'C', 'E'], ['D'], 1.0]
[['D', 'E'], ['A', 'C'], 1.0]
[['C', 'E'], ['D', 'A'], 1.0]
[['A', 'E'], ['D', 'C'], 1.0]
[['E'], ['D', 'A', 'C'], 1.0]


In [19]:
evals = get_lifts(confidence_test, frequent_test, len(test_df))


 [['B'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['C'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['A'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['D'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['E'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['B'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['D'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['E'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['E'], ['D'], 1.0]
lift 1.25
leverage 0.07999999999999996

 [['B', 'C'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['B', 'A'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['B'], ['A', 'C'], 1.0]
lift 1.0
leverage 0.0

 [['D', 'B'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['D', 'C'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['D', 'A'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['D'], ['A', 'C'], 1.0]
lift 1.0
leverage 0.0

 [['C', 'E'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['A', 'E'], ['C'], 1.0]
lift 1.0
leverage 0.0

 [['E'], ['A', 'C'], 1.0]
lift 1.0
leverage 0.0

 [['D', 'E'], ['A'], 1.0]
lift 1.0
leverage 0.0

 [['A', 'E'], ['D'], 1.0]
lift 1.25
leverage 0.

In [20]:
for row in evals[0]:
    print(row)

[['B'], ['A'], 1.0, 1.0, 0.0]
[['C'], ['A'], 1.0, 1.0, 0.0]
[['A'], ['C'], 1.0, 1.0, 0.0]
[['D'], ['A'], 1.0, 1.0, 0.0]
[['E'], ['A'], 1.0, 1.0, 0.0]
[['B'], ['C'], 1.0, 1.0, 0.0]
[['D'], ['C'], 1.0, 1.0, 0.0]
[['E'], ['C'], 1.0, 1.0, 0.0]
[['E'], ['D'], 1.0, 1.25, 0.07999999999999996]
[['B', 'C'], ['A'], 1.0, 1.0, 0.0]
[['B', 'A'], ['C'], 1.0, 1.0, 0.0]
[['B'], ['A', 'C'], 1.0, 1.0, 0.0]
[['D', 'B'], ['A'], 1.0, 1.0, 0.0]
[['D', 'C'], ['A'], 1.0, 1.0, 0.0]
[['D', 'A'], ['C'], 1.0, 1.0, 0.0]
[['D'], ['A', 'C'], 1.0, 1.0, 0.0]
[['C', 'E'], ['A'], 1.0, 1.0, 0.0]
[['A', 'E'], ['C'], 1.0, 1.0, 0.0]
[['E'], ['A', 'C'], 1.0, 1.0, 0.0]
[['D', 'E'], ['A'], 1.0, 1.0, 0.0]
[['A', 'E'], ['D'], 1.0, 1.25, 0.07999999999999996]
[['E'], ['D', 'A'], 1.0, 1.25, 0.07999999999999996]
[['D', 'B'], ['C'], 1.0, 1.0, 0.0]
[['D', 'E'], ['C'], 1.0, 1.0, 0.0]
[['C', 'E'], ['D'], 1.0, 1.25, 0.07999999999999996]
[['E'], ['D', 'C'], 1.0, 1.25, 0.07999999999999996]
[['D', 'B', 'C'], ['A'], 1.0, 1.0, 0.0]
[['D', 'B'

In [21]:
frequent_full = frequent_item_sets(adj_matrix, adj_matrix.columns, 3)

2
3
4
5
6
7
No Frequents


In [22]:
for key in frequent_full.keys():
    print('Item Set Length: ', key, '\n', frequent_full[key])

Item Set Length:  1 
 [['106', '22', '132', '135', '28', '171', '5', '165', '104', '82', '3', '122', '272', '264', '111', '19', '36', '54', '44', '70', '79', '45', '58', '99', '56', '24', '214', '131', '8', '81', '155', '42', '307', '202', '204', '74', '296', '144', '288', '61', '60', '49', '29', '270', '266', '85', '51', '40', '23', '52', '32', '63', '185', '278', '57', '178', '71', '138', '235', '294', '75', '113', '309', '158', '128', '86', '1', '93', '169', '38', '55', '27', '107', '167', '143', '26', '35', '14', '250', '177', '65', '80', '152', '64', '6', '2', '108', '154', '12', '148', '9', '269', '37', '13', '273', '77', '110', '183', '17', '53', '156', '46', '100', '160', '78', '308', '31', '34', '48', '102', '94', '30', '59', '157', '105', '310', '73', '72', '133', '175', '21', '164', '170', '265', '297', '268', '149', '146', '41', '182', '147', '10', '213', '97', '295', '179', '141', '50', '263', '76', '109', '176', '292'], [37.0, 5.0, 23.0, 8.0, 19.0, 13.0, 18.0, 18.0, 13.0,

In [23]:
confidence_full = get_association_rules(frequent_full, 1)

parent set:  ['106', '99'] 4.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['106', '93'] 6.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21

77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['171', '170'] 6.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['5', '99'] 3.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38


309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['122', '93'] 3.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['272', '99'] 4.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
14

94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['70', '179'] 3.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['45', '99'] 3.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2


202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['99', '169'] 9.0
f_set ['2', '2']
106
22
132
135
28
171
5
165
104
82
3
122
272
264
111
19
36
54
44
70
79
45
58
99
56
24
214
131
8
81
155
42
307
202
204
74
296
144
288
61
60
49
29
270
266
85
51
40
23
52
32
63
185
278
57
178
71
138
235
294
75
113
309
158
128
86
1
93
169
38
55
27
107
167
143
26
35
14
250
177
65
80
152
64
6
2
108
154
12
148
9
269
37
13
273
77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
parent set:  ['99', '27'] 3.0
f_set ['2', '2']
106
22
132
135
28
171
5
165

...

['178', '170', '176']
['178', '179', '176']
['71', '93', '143']
['71', '177', '72']
['138', '93', '143']
['138', '93', '177']
['138', '93', '175']
['138', '72', '175']
['138', '179', '176']
['294', '175', '176']
['158', '93', '143']
['158', '93', '177']
['158', '93', '100']
['158', '93', '160']
['158', '93', '102']
['158', '93', '175']
['158', '93', '170']
['158', '143', '100']
['158', '143', '175']
['158', '143', '176']
['158', '177', '72']
['158', '177', '175']
['158', '177', '176']
['158', '108', '100']
['158', '100', '72']
['158', '100', '175']
['158', '100', '179']
['158', '175', '170']
['158', '179', '176']
['128', '250', '175']
['86', '93', '143']
['86', '93', '100']
['86', '93', '175']
['86', '177', '72']
['86', '177', '175']
['86', '177', '170']
['86', '177', '176']
['86', '108', '175']
['86', '110', '175']
['86', '100', '175']
['86', '72', '175']
['86', '175', '170']
['86', '175', '176']
['93', '169', '143']
['93', '169', '177']
['93', '169', '100']
['93', '169', '72']
['93',

['5', '176']
['165', '99']
['165', '296']
['165', '86']
['165', '93']
['165', '297']
['104', '177']
['122', '24']
['122', '93']
['272', '99']
['272', '270']
['272', '86']
['272', '143']
['272', '177']
['272', '72']
['272', '170']
['272', '265']
['272', '176']
['19', '250']
['36', '108']
['36', '46']
['70', '99']
['70', '296']
['70', '138']
['70', '93']
['70', '169']
['70', '143']
['70', '177']
['70', '110']
['70', '100']
['70', '72']
['70', '175']
['70', '164']
['70', '170']
['70', '179']
['45', '99']
['45', '42']
['45', '143']
['45', '177']
['45', '175']
['45', '170']
['45', '176']
['58', '57']
['58', '177']
['58', '175']
['58', '176']
['99', '24']
['99', '81']
['99', '296']
['99', '270']
['99', '266']
['99', '278']
['99', '178']
['99', '71']
['99', '138']
['99', '294']
['99', '113']
['99', '158']
['99', '128']
['99', '86']
['99', '1']
['99', '93']
['99', '169']
['99', '27']
['99', '143']
['99', '26']
['99', '250']
['99', '177']
['99', '6']
['99', '108']
['99', '110']
['99', '46']
['9

77
110
183
17
53
156
46
100
160
78
308
31
34
48
102
94
30
59
157
105
310
73
72
133
175
21
164
170
265
297
268
149
146
41
182
147
10
213
97
295
179
141
50
263
76
109
176
292
f_set ['106', '93']
['106', '99']
['106', '93']
['106', '169']
['106', '143']
['106', '100']
['106', '175']
['106', '170']
['106', '147']
['106', '179']
['106', '76']
['106', '176']
['106', '292']
['171', '93']
['171', '169']
['171', '143']
['171', '175']
['171', '170']
['5', '99']
['5', '270']
['5', '86']
['5', '26']
['5', '177']
['5', '175']
['5', '176']
['165', '99']
['165', '296']
['165', '86']
['165', '93']
['165', '297']
['104', '177']
['122', '24']
['122', '93']
['272', '99']
['272', '270']
['272', '86']
['272', '143']
['272', '177']
['272', '72']
['272', '170']
['272', '265']
['272', '176']
['19', '250']
['36', '108']
['36', '46']
['70', '99']
['70', '296']
['70', '138']
['70', '93']
['70', '169']
['70', '143']
['70', '177']
['70', '110']
['70', '100']
['70', '72']
['70', '175']
['70', '164']
['70', '170']
[

['100', '147']
['100', '179']
['100', '50']
['100', '176']
['100', '292']
['160', '72']
['160', '175']
['160', '179']
['160', '176']
['34', '175']
['48', '175']
['48', '170']
['102', '72']
['102', '175']
['102', '170']
['102', '176']
['94', '175']
['94', '170']
['94', '179']
['94', '50']
['72', '175']
['72', '170']
['72', '265']
['72', '147']
['72', '179']
['72', '263']
['72', '176']
['175', '21']
['175', '164']
['175', '170']
['175', '265']
['175', '146']
['175', '41']
['175', '147']
['175', '179']
['175', '263']
['175', '176']
['175', '292']
['170', '146']
['170', '147']
['170', '179']
['170', '50']
['170', '176']
['170', '292']
['146', '179']
['146', '176']
['147', '179']
['147', '176']
['179', '176']
['179', '292']
['76', '176']
['176', '292']
f_set ['106', '169', '175']
['106', '93', '100']
['106', '169', '175']
['106', '100', '170']
['106', '175', '170']
['171', '169', '175']
['272', '99', '86']
['272', '270', '86']
['70', '99', '143']
['70', '99', '72']
['70', '138', '72']
['70'

['93', '143', '175', '170']
['93', '143', '170', '176']
['93', '100', '48', '170']
['93', '100', '94', '175']
['93', '100', '175', '170']
['93', '100', '170', '176']
['169', '143', '100', '175']
['169', '143', '100', '170']
['169', '143', '175', '170']
['169', '100', '175', '170']
['169', '72', '175', '170']
['143', '100', '175', '170']
['143', '100', '170', '176']
['143', '175', '170', '179']
['143', '175', '170', '176']
['177', '72', '175', '176']
['177', '175', '170', '176']
['177', '175', '179', '176']
X {'143', '175', '170', '100'} 6.0
{'143', '175', '170', '100'} -> {'93'} 0.8333333333333334
X {'170', '175', '100', '93'} 6.0
{'170', '175', '100', '93'} -> {'143'} 0.8333333333333334
X {'143', '175', '170', '93'} 7.0
{'143', '175', '170', '93'} -> {'100'} 0.7142857142857143
X {'143', '170', '100', '93'} 7.0
{'143', '170', '100', '93'} -> {'175'} 0.7142857142857143
X {'143', '175', '100', '93'} 9.0
{'143', '175', '100', '93'} -> {'170'} 0.5555555555555556
parent set:  ['169', '143',

In [24]:
for c in confidence_full:
    print(c)

[['138', '72'], ['70'], 1.0]
[['70', '138'], ['72'], 1.0]
[['70', '138'], ['175'], 1.0]
[['70', '169'], ['175'], 1.0]
[['70', '170'], ['175'], 1.0]
[['58', '176'], ['177'], 1.0]
[['143', '71'], ['99'], 1.0]
[['169', '86'], ['99'], 1.0]
[['27', '93'], ['99'], 1.0]
[['27', '99'], ['93'], 1.0]
[['26', '93'], ['99'], 1.0]
[['26', '99'], ['93'], 1.0]
[['143', '26'], ['99'], 1.0]
[['26', '99'], ['143'], 1.0]
[['42', '177'], ['175'], 1.0]
[['143', '51'], ['94'], 1.0]
[['50', '100'], ['51'], 1.0]
[['178', '94'], ['100'], 1.0]
[['178', '160'], ['176'], 1.0]
[['143', '71'], ['93'], 1.0]
[['138', '72'], ['175'], 1.0]
[['128', '250'], ['175'], 1.0]
[['143', '26'], ['93'], 1.0]
[['26', '93'], ['143'], 1.0]
[['143', '48'], ['93'], 1.0]
[['164', '93'], ['143'], 1.0]
[['156', '94'], ['93'], 1.0]
[['164', '93'], ['175'], 1.0]
[['143', '50'], ['94'], 1.0]
[['176', '110'], ['177'], 1.0]
[['102', '177'], ['175'], 1.0]
[['50', '100'], ['94'], 1.0]
[['175', '263'], ['72'], 1.0]
[['263', '72'], ['175'], 1.0]

In [25]:
evals_full, m = get_lifts(confidence_full, frequent_full, len(adj_matrix))


 [['138', '72'], ['70'], 1.0]
lift 38.943396226415096
leverage 0.0014161652695150531

 [['70', '138'], ['72'], 1.0]
lift 20.038834951456312
leverage 0.0013809547953848927

 [['70', '138'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['70', '169'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['70', '170'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['58', '176'], ['177'], 1.0]
lift 10.75
leverage 0.0017577068685776095

 [['143', '71'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['169', '86'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['27', '93'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['27', '99'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['26', '93'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['26', '99'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['143',

In [26]:
for row in evals_full:
    print(row)

[['138', '72'], ['70'], 1.0, 38.943396226415096, 0.0014161652695150531]
[['70', '138'], ['72'], 1.0, 20.038834951456312, 0.0013809547953848927]
[['70', '138'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['70', '169'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['70', '170'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['58', '176'], ['177'], 1.0, 10.75, 0.0017577068685776095]
[['143', '71'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['169', '86'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['27', '93'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['27', '99'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['26', '93'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['26', '99'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['143', '26'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['26', '99'], ['143'], 1.0, 13.063291139240507, 0.0013422232738417163]
[['42', '177'], ['175'], 1.0, 7.50

In [27]:
for row in m:
    print(row)

[38.943396226415096, 0.0014161652695150531]
[20.038834951456312, 0.0013809547953848927]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598307643771408]
[10.75, 0.0017577068685776095]
[15.518796992481203, 0.0013598285109067965]
[15.518796992481203, 0.0013598285109067965]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[15.518796992481203, 0.0013598285109067965]
[13.063291139240507, 0.0013422232738417163]
[7.505454545454546, 0.0012598307643771408]
[58.971428571428575, 0.001428841040201911]
[114.66666666666667, 0.0014408126014061654]
[13.578947368421051, 0.0013464485307373355]
[6.573248407643312, 0.0012323665945556156]
[10.32, 0.0013126464755723814]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598307643771408]
[10.32, 0.0013126464755723814]
[13.063291139240507, 0.0013422232738417163]
[10.32, 0.0013126